# FTMS Visualisation Tool v0.1

### Author: Will Kew
#### Date: June 2016
##### Email will.kew@gmail.com

    Copyright Will Kew, 2016

    This file is part of FTMS Visualisation (also known as i-van Krevelen).

    FTMS Visualisation is free software: you can redistribute it and/or modify
    it under the terms of the GNU General Public License as published by
    the Free Software Foundation, either version 3 of the License, or
    (at your option) any later version.

    FTMS Visualisation is distributed in the hope that it will be useful,
    but WITHOUT ANY WARRANTY; without even the implied warranty of
    MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
    GNU General Public License for more details.

    You should have received a copy of the GNU General Public License
    along with FTMS Visualisation.  If not, see <http://www.gnu.org/licenses/>.

## Visualise full-resolution FTMS spectra and assignments

This notebook will read in the data, produce some van krevelen and DBE vs C# plots, and show the full resolution spectra too.

This first section loads up the necessary packages and defines a few things, also reads in the profile data

**Prerequisites** are listed below, but most notably you will need to install datashader from source.

Note - This may not work with recent versions of matplotlib. IT has been tested on Python 3, and previous versions on python 2.  
Code here is provided as a proof-of-concept rather than production level code.

Download from github - https://github.com/bokeh/datashader , extract the zip

In a command line/terminal, go to the extracted files and enter the command:
```
python setup.py install
```

In [2]:
import pandas as pd
import numpy as np
import xarray as xr
import datashader as ds
import datashader.transfer_functions as tf
from datashader.bokeh_ext import InteractiveImage

from IPython.core.display import HTML, display

import math, os

import bokeh.plotting as bp
import bokeh.palettes as bpal

from bokeh.plotting import figure, show, output_file, gridplot, hplot
from bokeh.models import HoverTool, ColumnDataSource, OpenURL, TapTool, Rect, Range1d
from bokeh.models.mappers import LinearColorMapper
from bokeh.models.widgets import Panel, Tabs

from collections import OrderedDict


In [4]:
import sys
#We import also the FTMSVizProcessingModule which contains a few useful functions.
#here we define where the scripts are stored. 
### !!!!!!!!! Make sure to change this to where you have saved these scripts. !!!!!!!!!!!#######
try: #test if running in ipython
    __IPYTHON__
except NameError: #if not running in ipython....
    import FTMSVizProcessingModule as FTPM
    path  = os.getcwd()+"data\\" #example data location
else: #if running in ipython
    #homepath
    #scriptlocation = "C:\\Users\\Will\\Dropbox\\Documents\\University\\Edinburgh\\Coding\\Python3\\FTMS\\DataProcessingScripts"
    #OfficeDesktopPath
    scriptlocation = "F:\\Will\\Dropbox\\Documents\\University\\Edinburgh\\Coding\\Python3\FTMS\\DataProcessingScripts"
    sys.path.append(scriptlocation)
    import FTMSVizProcessingModule as FTPM
    #OfficeDesktopPath
    path = "F:\\Will\\Dropbox\\Documents\\University\\Edinburgh\\Coding\\Python3\\FTMS\\DataProcessingScripts\\data\\"
    dictionarypath= "F:\\Will\\Dropbox\\Documents\\University\\Edinburgh\\Coding\\Python3\FTMS\\DataProcessingScripts\\MassToFormula\\dictionaries\\"
    #HomeDesktopPath
    #path = "C:\\Users\\Will\\Dropbox\\Documents\\University\\Edinburgh\\Coding\\Python3\\FTMS\\DataProcessingScripts\\data\\"
    #dictionarypath= "C:\\Users\\Will\\Dropbox\\Documents\\University\\Edinburgh\\Coding\\Python3\FTMS\\DataProcessingScripts\\MassToFormula\\dictionaries\\"


In [5]:
bp.output_notebook()

df = pd.read_csv('data/RawData/SRFA.xy',sep=" ",header=None,names=["mz","RelAbun"])
inputfile = "data/OutputCSV/SRFA-hits.csv"
isolist = "data/OutputCSV/SRFA-isohits.csv"
nohitslist = "data/OutputCSV/SRFA-nohits.csv"
x_range=(min(df["mz"]),max(df["mz"]))
y_range=(min(df["RelAbun"]),max(df["RelAbun"]))

   
options = dict(line_color='blue')

display(HTML("<style>.container { width:90% !important; }</style>"))

Loading BokehJS ...

In [6]:
data,hetclassintdf = FTPM.mycsvreader(inputfile)
isodata = FTPM.isocsvreader(isolist)
nodata = FTPM.nohitsreader(nohitslist)

#data.tail(10)
#isodata.tail(10)
#nodata.tail(10)

In [7]:
#glocmap = cm.inferno_r
#colors = ["#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*glocmap(matplotlib.colors.Normalize()(np.linspace(0,max(data["mz"]),len(data["mz"]))))]
glocmap = list(bpal.Viridis10)
glocmap2 = list(bpal.Inferno8)

glocmap.reverse()
glocmap2.reverse()



source = ColumnDataSource(data)
isosource = ColumnDataSource(isodata)
nosource = ColumnDataSource(nodata)

url = "http://www.chemspider.com/Search.aspx?q=@Formula"
TOOLS="resize,crosshair,pan,wheel_zoom,box_zoom,undo,redo,reset,tap,previewsave,box_select,poly_select,lasso_select,hover"

In [8]:
width = 1200
height = 600
def create_image(x_range=x_range, y_range=y_range, w=width, h=height):
    cvs = ds.Canvas(x_range=x_range, y_range=y_range, plot_height=h, plot_width=w)
    agg = cvs.line(df, 'mz', 'RelAbun', agg=ds.any())
    #return tf.interpolate(agg) #deprecated
    return tf.shade(agg,cmap=["darkblue"]) 


def base_plot(tools='pan,wheel_zoom,reset'):
    p = bp.figure(tools=TOOLS, plot_width=width, plot_height=height,
        x_range=x_range, y_range=y_range, outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0)   
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p

In [9]:
p = base_plot()

p.scatter(x='mz', y='RA',source=source,fill_color='black',line_color=None)
hover = p.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([('Formula', "@Formula"),('Mass',"@mz{1.11111}"),('Error (ppm)',"@Error{1.11}")])

p.scatter(x='mz', y='RA',source=isosource,fill_color='green',line_color=None)
p.scatter(x='mz', y='RA',source=nosource,fill_color='red',line_color=None)

taptool = p.select(type=TapTool)
taptool.callback = OpenURL(url=url)
InteractiveImage(p, create_image)


In [6]:
""" #THIS CELL IS DEPRECATED AND BROKEN
p1 = figure(tools=TOOLS,width=800, height=600, x_axis_label='O/C',y_axis_label='H/C',webgl=True)
colors = ["#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*glocmap(matplotlib.colors.Normalize()(np.linspace(0,max(data["mz"]),len(data["mz"]))))]
color_mapper = LinearColorMapper(palette=glocmap, low=msxlim[0], high=msxlim[1])

p1.scatter(x='OC', y='HC',source=source,radius='VKRadii', fill_color=colors, fill_alpha=0.75,line_color=None)
hover = p1.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([('Formula', "@Formula"),('Mass',"@mz{1.11111}"),('Error (ppm)',"@Error{1.11}")])
taptool = p1.select(type=TapTool)
taptool.callback = OpenURL(url=url)
#tab1 = Panel(child=p1, title="Van Krevelen")

p2 = figure(tools=TOOLS,width=800, height=600, x_axis_label='C#',y_axis_label='DBE',webgl=True)
colors = ["#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*glocmap(matplotlib.colors.Normalize()(np.linspace(0,max(data["Ono"]),len(data["Ono"]))))]
p2.scatter(x='Cno', y='DBE',source=source,radius='DBERadii', fill_color=colors, fill_alpha=0.75,line_color=None)
hover = p2.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([('Formula', "@Formula"),('Mass',"@mz{1.11111}"),('Error (ppm)',"@Error{1.11}")])
taptool = p2.select(type=TapTool)
taptool.callback = OpenURL(url=url)
#tab2 = Panel(child=p2, title="DBE vs Carbon Number Plot")

p3 = figure(tools=TOOLS,width=800, height=600, x_axis_label='m/z',y_axis_label='Rel Abun')
p3.line(x='mz', y='RA',source=source)
p3.scatter(x='mz', y='RA',source=source,fill_color='black',line_color=None)
hover = p3.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([('Formula', "@Formula"),('Mass',"@mz{1.11111}"),('Error (ppm)',"@Error{1.11}")])
taptool = p3.select(type=TapTool)
taptool.callback = OpenURL(url=url)

p4 = figure(tools=TOOLS,width=800, height=600, x_axis_label='m/z',y_axis_label='Rel Abun')
p4.line(x='mz', y='RA',source=source)
p4.scatter(x='mz', y='RA',source=source,fill_color='black',line_color=None)
hover = p4.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([('Formula', "@Formula"),('Mass',"@mz{1.11111}"),('Error (ppm)',"@Error{1.11}")])
taptool = p4.select(type=TapTool)
taptool.callback = OpenURL(url=url)


t1 = hplot(p1,p3)
t2 = hplot(p2,p4)
tab1 = Panel(child=t1, title="Van Krevelen")
tab2 = Panel(child=t2, title="DBE vs Carbon Number Plot")
tabs = Tabs(tabs=[ tab1, tab2 ])
#show(tabs)
"""

'\np1 = figure(tools=TOOLS,width=800, height=600, x_axis_label=\'O/C\',y_axis_label=\'H/C\',webgl=True)\ncolors = ["#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*glocmap(matplotlib.colors.Normalize()(np.linspace(0,max(data["mz"]),len(data["mz"]))))]\ncolor_mapper = LinearColorMapper(palette=glocmap, low=msxlim[0], high=msxlim[1])\n\np1.scatter(x=\'OC\', y=\'HC\',source=source,radius=\'VKRadii\', fill_color=colors, fill_alpha=0.75,line_color=None)\nhover = p1.select(dict(type=HoverTool))\nhover.tooltips = OrderedDict([(\'Formula\', "@Formula"),(\'Mass\',"@mz{1.11111}"),(\'Error (ppm)\',"@Error{1.11}")])\ntaptool = p1.select(type=TapTool)\ntaptool.callback = OpenURL(url=url)\n#tab1 = Panel(child=p1, title="Van Krevelen")\n\np2 = figure(tools=TOOLS,width=800, height=600, x_axis_label=\'C#\',y_axis_label=\'DBE\',webgl=True)\ncolors = ["#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*glocmap(matplotlib.colors.Normalize()(np.linspace(0,max(data["Ono"]),len(d